# Learning regression datasets and training model

### Imports

In [128]:
import os
from pathlib import Path
import xgboost as xgb
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.model_selection import RandomizedSearchCV, GridSearchCV

In [129]:
while "notebooks" in os.getcwd():
    os.chdir("../")

In [130]:
do_training = True

### California Housing Prices Datset

In [70]:
DATA_DIR = Path('data/housing_data')
file_name = 'housing.csv'
scaled_file_name = 'housing_scaled.csv'
train_file_name = 'train_housing_scaled.csv'
test_file_name = 'test_housing_scaled.csv'
scaler_params_file = 'housing_scaling_params.csv'

In [71]:
MODEL_PATH = Path('models/')
housing_model_name = 'housing_scaled'

In [72]:
df = pd.read_csv(DATA_DIR / file_name)

In [73]:

df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20640 entries, 0 to 20639
Data columns (total 10 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   longitude           20640 non-null  float64
 1   latitude            20640 non-null  float64
 2   housing_median_age  20640 non-null  float64
 3   total_rooms         20640 non-null  float64
 4   total_bedrooms      20433 non-null  float64
 5   population          20640 non-null  float64
 6   households          20640 non-null  float64
 7   median_income       20640 non-null  float64
 8   median_house_value  20640 non-null  float64
 9   ocean_proximity     20640 non-null  object 
dtypes: float64(9), object(1)
memory usage: 1.6+ MB


In [74]:
df.ocean_proximity.unique()

array(['NEAR BAY', '<1H OCEAN', 'INLAND', 'NEAR OCEAN', 'ISLAND'],
      dtype=object)

In [75]:
df = df.drop(columns=['ocean_proximity'])

In [76]:
df.loc[:, df.columns == 'median_house_value']

median_house_value
0                452600.0
1                358500.0
2                352100.0
3                341300.0
4                342200.0
...                   ...
20635             78100.0
20636             77100.0
20637             92300.0
20638             84700.0
20639             89400.0

[20640 rows x 1 columns]

In [77]:
def scale_split_df(_df: pd.DataFrame, prediction_column: str, test_size: float, data_dir: Path,
                   scaled_df_name: str, train_df_name: str, test_df_name: str, scaler_params_name: str):

    scaler = StandardScaler()
    features_df = df.loc[:, df.columns != prediction_column]
    prediction_df = df.loc[:, df.columns == prediction_column]
    scaled_features = pd.DataFrame(scaler.fit_transform(features_df))
    scaled_features.columns = features_df.columns.str.replace(' ', '_')
    scaled_df = pd.concat([scaled_features, prediction_df], axis=1)
    train_df, test_df = train_test_split(scaled_df, test_size=test_size)

    scaled_df.to_csv(data_dir/scaled_df_name, index=False)
    train_df.to_csv(data_dir/train_df_name, index=False)
    test_df.to_csv(data_dir/test_df_name, index=False)

    normalization_params = {
        "mean": scaler.mean_,
        "variance": scaler.var_,
    }

    normalization_params_df = pd.DataFrame.from_dict(
        normalization_params, orient="index")
    normalization_params_df.columns = features_df.columns
    normalization_params_df.to_csv(DATA_DIR/scaler_params_name)

    return scaled_df, train_df, test_df

In [78]:
df = df.dropna()

In [79]:
scaled_df, train_df, test_df = scale_split_df(
    df, 'median_house_value', 0.2, DATA_DIR, scaled_file_name, train_file_name, test_file_name, scaler_params_file)
scaled_df.describe()

longitude      latitude  housing_median_age   total_rooms  \
count  2.043300e+04  2.043300e+04        2.043300e+04  2.043300e+04   
mean  -8.457103e-16  1.535632e-15        4.451107e-17 -3.651299e-17   
std    1.000024e+00  1.000024e+00        1.000024e+00  1.000024e+00   
min   -2.385447e+00 -1.447937e+00       -2.194584e+00 -1.205604e+00   
25%   -1.112692e+00 -7.972780e-01       -8.444662e-01 -5.429688e-01   
50%    5.393926e-01 -6.428050e-01        2.913923e-02 -2.331597e-01   
75%    7.789699e-01  9.768213e-01        6.644886e-01  2.317829e-01   
max    2.625711e+00  2.956885e+00        1.855769e+00  1.678713e+01   

       total_bedrooms    population    households  median_income  \
count    2.043300e+04  2.043300e+04  2.043300e+04   2.043300e+04   
mean    -7.372146e-17 -8.345826e-17 -6.398466e-17   3.060136e-16   
std      1.000024e+00  1.000024e+00  1.000024e+00   1.000024e+00   
min     -1.274093e+00 -1.254828e+00 -1.303810e+00  -1.775054e+00   
25%     -5.740034e-01 -5.629702e-01 -5.739976e-01  -6.884113e-01   
50%     -2.441308e-01 -2.285134e-01 -2.365573e-01  -1.762077e-01   
75%      2.589843e-01  2.621409e-01  2.735268e-01   4.595713e-01   
max      1.401871e+01  3.023088e+01  1.460297e+01   5.859665e+00   

       median_house_value  
count        20433.000000  
mean        206864.413155  
std         115435.667099  
min          14999.000000  
25%         119500.000000  
50%         179700.000000  
75%         264700.000000  
max         500001.000000

In [80]:
train_df = pd.read_csv("data/housing_data/train_housing_scaled.csv")
test_df = pd.read_csv("data/housing_data/test_housing_scaled.csv")

In [81]:
X_train = train_df.loc[:, df.columns != 'median_house_value']
y_train = train_df.loc[:, df.columns == 'median_house_value']#/10000
X_test = test_df.loc[:, df.columns != 'median_house_value']
y_test = test_df.loc[:, df.columns == 'median_house_value']#/10000

#### Housing model training

In [82]:
def train_and_save_model(param: dict, steps: int, dtrain: xgb.DMatrix, dtest: xgb.DMatrix, model_path: Path, model_name: str):
    if do_training:
        gbdt_model = xgb.train(param, dtrain,
                               evals=[(dtest, 'test'), (dtrain, 'train')],
                               verbose_eval=50, early_stopping_rounds=1, num_boost_round=steps
                               )
    if do_training:
        gbdt_model.dump_model(
            model_path / f"{model_name}_dumped.txt", with_stats=True)
        gbdt_model.save_model(model_path / f"{model_name}_saved.json")
    else:
        gbdt_model = xgb.Booster()
        gbdt_model.load_model(model_path / f"{model_name}_saved.json")
    return gbdt_model

#### Performing grid_search

In [83]:
def grid_search(space: dict, X_train: pd.DataFrame, y_train: pd.DataFrame, X_test: pd.DataFrame, y_test: pd.DataFrame,
                num_boost_round = 300):
    clf = xgb.XGBRegressor(
        objective='reg:squarederror',
        early_stopping_rounds=10,
        #n_boost_rounds=30
        n_estimators = num_boost_round
) 
    grid_search = GridSearchCV(
        clf, param_grid=space, scoring='neg_root_mean_squared_error', n_jobs=4, cv=5, verbose = 0)
    grid_search.fit(X_train, y_train, eval_set=[(X_test, y_test)], verbose = 0)
    return grid_search

In [84]:
def search_hyperparameters_and_save_model(search_space: dict, 
                                          X_train: pd.DataFrame, 
                                          y_train: pd.DataFrame,
                                          X_test: pd.DataFrame, 
                                          y_test: pd.DataFrame,
                                          model_name: str,
                                          MODEL_PATH: Path,
                                          num_boost_round = 300):
    best = grid_search(search_space, X_train, y_train, X_test, y_test, num_boost_round=num_boost_round)

    best_params = best.best_params_
    dump = best.best_estimator_.get_booster().get_dump()
    leaves = sum([i.count('leaf') for i in dump])
    iterations = len(dump)
    dtrain = xgb.DMatrix(X_train, label=y_train)
    dtest = xgb.DMatrix(X_test, label=y_test)
    name =  "different_sizes/" + model_name +  f"_leaves_{leaves}"
    train_and_save_model(best_params, iterations, dtrain, dtest, MODEL_PATH, name)

#### Training models with various sizes - depth is set to be fixed to control size of a model


In [85]:
grid_params = {
    'max_depth': [1, 2,],# 3, 4],
    'eta': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9],
    'subsample': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
}

In [86]:
for d in range(1, 10):
    grid_params['max_depth'] = [d] 
    search_hyperparameters_and_save_model(grid_params,
                                      X_train,
                                      y_train, 
                                      X_test, 
                                      y_test,
                                      housing_model_name,
                                      MODEL_PATH);

/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:384: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype):
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:359: FutureWarning: is_categorical_dtype is deprecated and will be removed in a

ValueError: 
All the 500 fits failed.
It is very likely that your model is misconfigured.
You can try to debug the error by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
42 fits failed with the following error:
Traceback (most recent call last):
  File "/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/sklearn/model_selection/_validation.py", line 729, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/core.py", line 729, in inner_f
    return func(**kwargs)
  File "/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/sklearn.py", line 1051, in fit
    train_dmatrix, evals = _wrap_evaluation_matrices(
  File "/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/sklearn.py", line 534

#### Two best models - depth is included in grid search 

In [ ]:
grid_params = {
    'max_depth': [1, 2, 3, 4],
    'eta': [0.01],#, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9],
    'subsample': [0.01]#, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
}

In [ ]:
grid_params_big = {
    'max_depth': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10],
    'eta': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9],
    'subsample': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
}

In [ ]:
%%time
best = grid_search(grid_params, X_train, y_train, X_test, y_test, num_boost_round=40)

In [ ]:
%%time
best_big = grid_search(grid_params_big, X_train, y_train, X_test, y_test, num_boost_round = 20)

In [ ]:
best.best_params_

{'eta': 0.01, 'max_depth': 4, 'subsample': 0.01}

In [ ]:
len(best.best_estimator_.get_booster().get_dump())

40

In [ ]:
best_big.best_params_

{'eta': 0.2, 'max_depth': 10, 'subsample': 0.9}

In [ ]:
len(best_big.best_estimator_.get_booster().get_dump())

20

In [ ]:
# training hyperparameters
param = {
    'eta': 0.1,
    'max_depth': 4,
    'objective': 'reg:squarederror',
    'seed': 42,
    'subsample': 0.01,
}
steps = 40

In [ ]:
# training hyperparameters
param_big = {
    'eta': 0.2,
    'max_depth': 10,
    'objective': 'reg:squarederror',
    'seed': 42,
    'subsample': 0.9,
}
steps = 1

In [ ]:
dtrain = xgb.DMatrix(X_train, label=y_train)
dtest = xgb.DMatrix(X_test, label=y_test)

/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:384: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype):
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:359: FutureWarning: is_categorical_dtype is deprecated and will be removed in a

In [ ]:
%%time
train_and_save_model(param, steps, dtrain, dtest, MODEL_PATH, housing_model_name)

[0]	test-rmse:11.25719	train-rmse:10.97680
[39]	test-rmse:6.54802	train-rmse:6.28841
CPU times: user 2.98 s, sys: 6.59 ms, total: 2.99 s
Wall time: 221 ms


In [ ]:
%%time
train_and_save_model(param_big, steps, dtrain, dtest, MODEL_PATH, housing_model_name + '_big')

[0]	test-rmse:100785.67308	train-rmse:96867.96499
CPU times: user 3.87 s, sys: 7.02 ms, total: 3.88 s
Wall time: 278 ms


### Single tree

In [ ]:
grid_params = {
    'max_depth': [3],
    'eta': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9],
    'subsample': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
}

In [ ]:
%%time
best = grid_search(grid_params, X_train, y_train, X_test, y_test, num_boost_round = 1)

/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:384: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype):
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:359: FutureWarning: is_categorical_dtype is deprecated and will be removed in a

CPU times: user 744 ms, sys: 90 ms, total: 834 ms
Wall time: 4.27 s


/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:384: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype):
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:359: FutureWarning: is_categorical_dtype is deprecated and will be removed in a

In [ ]:
best.best_params_

{'eta': 0.9, 'max_depth': 3, 'subsample': 0.9}

In [ ]:
len(best.best_estimator_.get_booster().get_dump())

1

In [ ]:
# training hyperparameters
param = {
    'eta': 0.9,
    'max_depth': 3,
    'objective': 'reg:squarederror',
    'seed': 42,
    'subsample': 0.9,
}
steps = 1

In [ ]:
%%time
train_and_save_model(param, steps, dtrain, dtest, MODEL_PATH, housing_model_name + '_single')

[0]	test-rmse:81710.35211	train-rmse:82611.51414
CPU times: user 992 ms, sys: 0 ns, total: 992 ms
Wall time: 76.5 ms


### Red Wine Dataset

In [ ]:
DATA_DIR = Path('data/wine_quality')
file_name = 'winequality_red.csv'
scaled_file_name = 'winequality_red_scaled.csv'
train_file_name = 'train_winequality_red_scaled.csv'
test_file_name = 'test_winequality_red_scaled.csv'
scaler_params_file = 'winequality_red_scaling_params.csv'
MODEL_PATH = Path('models/')
wine_model_name = 'winequality_red'

In [ ]:
df = pd.read_csv(DATA_DIR / file_name, sep=';')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1599 entries, 0 to 1598
Data columns (total 12 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   fixed acidity         1599 non-null   float64
 1   volatile acidity      1599 non-null   float64
 2   citric acid           1599 non-null   float64
 3   residual sugar        1599 non-null   float64
 4   chlorides             1599 non-null   float64
 5   free sulfur dioxide   1599 non-null   float64
 6   total sulfur dioxide  1599 non-null   float64
 7   density               1599 non-null   float64
 8   pH                    1599 non-null   float64
 9   sulphates             1599 non-null   float64
 10  alcohol               1599 non-null   float64
 11  quality               1599 non-null   int64  
dtypes: float64(11), int64(1)
memory usage: 150.0 KB


In [ ]:
#scaled_df, train_df, test_df = scale_split_df(
#    df, 'quality', 0.2, DATA_DIR, scaled_file_name, train_file_name, test_file_name, scaler_params_file)
#scaled_df.describe()

fixed_acidity  volatile_acidity   citric_acid  residual_sugar  \
count   1.599000e+03      1.599000e+03  1.599000e+03    1.599000e+03   
mean    3.554936e-16      1.733031e-16 -8.887339e-17   -1.244227e-16   
std     1.000313e+00      1.000313e+00  1.000313e+00    1.000313e+00   
min    -2.137045e+00     -2.278280e+00 -1.391472e+00   -1.162696e+00   
25%    -7.007187e-01     -7.699311e-01 -9.293181e-01   -4.532184e-01   
50%    -2.410944e-01     -4.368911e-02 -5.636026e-02   -2.403750e-01   
75%     5.057952e-01      6.266881e-01  7.652471e-01    4.341614e-02   
max     4.355149e+00      5.877976e+00  3.743574e+00    9.195681e+00   

          chlorides  free_sulfur_dioxide  total_sulfur_dioxide       density  \
count  1.599000e+03         1.599000e+03          1.599000e+03  1.599000e+03   
mean   3.732682e-16        -6.221137e-17          4.443669e-17 -3.473172e-14   
std    1.000313e+00         1.000313e+00          1.000313e+00  1.000313e+00   
min   -1.603945e+00        -1.422500e+00         -1.230584e+00 -3.538731e+00   
25%   -3.712290e-01        -8.487156e-01         -7.440403e-01 -6.077557e-01   
50%   -1.799455e-01        -1.793002e-01         -2.574968e-01  1.760083e-03   
75%    5.384542e-02         4.901152e-01          4.723184e-01  5.768249e-01   
max    1.112703e+01         5.367284e+00          7.375154e+00  3.680055e+00   

                 pH     sulphates       alcohol      quality  
count  1.599000e+03  1.599000e+03  1.599000e+03  1599.000000  
mean   2.861723e-15  6.754377e-16  1.066481e-16     5.636023  
std    1.000313e+00  1.000313e+00  1.000313e+00     0.807569  
min   -3.700401e+00 -1.936507e+00 -1.898919e+00     3.000000  
25%   -6.551405e-01 -6.382196e-01 -8.663789e-01     5.000000  
50%   -7.212705e-03 -2.251281e-01 -2.093081e-01     6.000000  
75%    5.759223e-01  4.240158e-01  6.354971e-01     6.000000  
max    4.528282e+00  7.918677e+00  4.202453e+00     8.000000

In [ ]:
train_df = pd.read_csv("data/wine_quality/train_winequality_red_scaled.csv")
test_df = pd.read_csv("data/wine_quality/test_winequality_red_scaled.csv")

In [ ]:
X_train = train_df.loc[:, train_df.columns != 'quality']
y_train = train_df.loc[:, train_df.columns == 'quality']
X_test = test_df.loc[:, test_df.columns != 'quality']
y_test = test_df.loc[:, test_df.columns == 'quality']

### Wine model training


#### Grid search

In [ ]:
grid_params = {
    'max_depth': [1, 2, 3, 4],
    'eta': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9],
    'subsample': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
}

In [ ]:
for d in range(1, 10):
    grid_params['max_depth'] = [d] 
    search_hyperparameters_and_save_model(grid_params,
                                      X_train,
                                      y_train, 
                                      X_test, 
                                      y_test,
                                      wine_model_name,
                                      MODEL_PATH)

In [ ]:
grid_params = {
    'max_depth': [1, 2, 3, 4],
    'eta': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9],
    'subsample': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
}

In [ ]:
grid_params_big = {
    'max_depth': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10],
    'eta': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9],
    'subsample': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
}

In [ ]:
%%time
best = grid_search(grid_params, X_train, y_train, X_test, y_test, num_boost_round=40)

In [ ]:
%%time
best_big = grid_search(grid_params_big, X_train, y_train, X_test, y_test, num_boost_round =20)

In [ ]:
best.best_params_

{'eta': 0.2, 'max_depth': 4, 'subsample': 0.9}

In [ ]:
len(best.best_estimator_.get_booster().get_dump())

40

In [ ]:
best_big.best_params_

{'eta': 0.2, 'max_depth': 6, 'subsample': 0.9}

In [ ]:
len(best_big.best_estimator_.get_booster().get_dump())

20

In [ ]:
# training hyperparameters
param = {
    'eta': 0.2,
    'max_depth': 4,
    'objective': 'reg:squarederror',
    'seed': 42,
    'subsample': 0.8
}
steps = 40

In [ ]:
# training hyperparameters
param_big = {
    'eta': 0.2,
    'max_depth': 6,
    'objective': 'reg:squarederror',
    'seed': 42,
    'subsample': 0.9
}
steps = 20

In [ ]:
dtrain = xgb.DMatrix(X_train, label=y_train)
dtest = xgb.DMatrix(X_test, label=y_test)

/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:384: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype):
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:359: FutureWarning: is_categorical_dtype is deprecated and will be removed in a

In [ ]:
train_and_save_model(param, steps, dtrain, dtest, MODEL_PATH, wine_model_name)

[0]	test-rmse:0.77840	train-rmse:0.74013
[31]	test-rmse:0.62305	train-rmse:0.45214


In [ ]:
train_and_save_model(param_big, steps, dtrain, dtest, MODEL_PATH, wine_model_name + "_big")

[0]	test-rmse:0.76863	train-rmse:0.71958


[19]	test-rmse:0.59941	train-rmse:0.34475


### Single tree

In [ ]:
grid_params = {
    'max_depth': [3],
    'eta': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9],
    'subsample': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
}

In [ ]:
%%time
best = grid_search(grid_params, X_train, y_train, X_test, y_test, num_boost_round = 1)

In [ ]:
best.best_params_

{'eta': 0.9, 'max_depth': 3, 'subsample': 0.9}

In [ ]:
len(best.best_estimator_.get_booster().get_dump())

1

In [ ]:
# training hyperparameters
param = {
    'eta': 0.9,
    'max_depth': 3,
    'objective': 'reg:squarederror',
    'seed': 42,
    'subsample': 0.9,
}
steps = 1

In [ ]:
%%time
train_and_save_model(param, steps, dtrain, dtest, MODEL_PATH, wine_model_name + '_single')

[0]	test-rmse:0.65343	train-rmse:0.66162
CPU times: user 2.21 s, sys: 6.17 ms, total: 2.22 s
Wall time: 169 ms


#### Mniejsze modele (maks. głębokość 4 zamiast 10) mają trochę gorsze wyniki ale mają znacznie mniej liści:
- Housing  RMSE: 51 51393.33848 vs 47937.65673, spadek liczby liści z ok 20 0000 do 1500
- Wine  RSE: 0.61376 vs 0.63269, spadek liczby liści z ok. 15 000 do 600

## Parkinsons Telemonitoring

### Dataset

In [298]:

DATA_DIR = Path('data/telemetry')
file_name = 'parkinsons_updrs.data'
scaled_file_name = 'telemetry_scaled.csv'
train_file_name = 'train_telemetry_scaled.csv'
test_file_name = 'test_telemetry_scaled.csv'
scaler_params_file = 'telemetry_scaling_params.csv'
MODEL_PATH = Path('models/')
telemetry_model_name = 'telemetry'

In [299]:
df = pd.read_csv(DATA_DIR / file_name, sep=',')
df.columns = df.columns.str.replace("[:]", "_", regex=True)
df.columns = df.columns.str.replace("[()]", "_", regex=True)
df.columns = df.columns.str.replace("[%]", "8", regex=True)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5875 entries, 0 to 5874
Data columns (total 22 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   subject#       5875 non-null   int64  
 1   age            5875 non-null   int64  
 2   sex            5875 non-null   int64  
 3   test_time      5875 non-null   float64
 4   motor_UPDRS    5875 non-null   float64
 5   total_UPDRS    5875 non-null   float64
 6   Jitter_8_      5875 non-null   float64
 7   Jitter_Abs_    5875 non-null   float64
 8   Jitter_RAP     5875 non-null   float64
 9   Jitter_PPQ5    5875 non-null   float64
 10  Jitter_DDP     5875 non-null   float64
 11  Shimmer        5875 non-null   float64
 12  Shimmer_dB_    5875 non-null   float64
 13  Shimmer_APQ3   5875 non-null   float64
 14  Shimmer_APQ5   5875 non-null   float64
 15  Shimmer_APQ11  5875 non-null   float64
 16  Shimmer_DDA    5875 non-null   float64
 17  NHR            5875 non-null   float64
 18  HNR     

In [300]:
df.head()

subject#  age  sex  test_time  motor_UPDRS  total_UPDRS  Jitter_8_  \
0         1   72    0     5.6431       28.199       34.398    0.00662   
1         1   72    0    12.6660       28.447       34.894    0.00300   
2         1   72    0    19.6810       28.695       35.389    0.00481   
3         1   72    0    25.6470       28.905       35.810    0.00528   
4         1   72    0    33.6420       29.187       36.375    0.00335   

   Jitter_Abs_  Jitter_RAP  Jitter_PPQ5  ...  Shimmer_dB_  Shimmer_APQ3  \
0     0.000034     0.00401      0.00317  ...        0.230       0.01438   
1     0.000017     0.00132      0.00150  ...        0.179       0.00994   
2     0.000025     0.00205      0.00208  ...        0.181       0.00734   
3     0.000027     0.00191      0.00264  ...        0.327       0.01106   
4     0.000020     0.00093      0.00130  ...        0.176       0.00679   

   Shimmer_APQ5  Shimmer_APQ11  Shimmer_DDA       NHR     HNR     RPDE  \
0       0.01309        0.01662      0.04314  0.014290  21.640  0.41888   
1       0.01072        0.01689      0.02982  0.011112  27.183  0.43493   
2       0.00844        0.01458      0.02202  0.020220  23.047  0.46222   
3       0.01265        0.01963      0.03317  0.027837  24.445  0.48730   
4       0.00929        0.01819      0.02036  0.011625  26.126  0.47188   

       DFA      PPE  
0  0.54842  0.16006  
1  0.56477  0.10810  
2  0.54405  0.21014  
3  0.57794  0.33277  
4  0.56122  0.19361  

[5 rows x 22 columns]

In [301]:
df = df.drop(columns=["subject#", "sex", "age", "total_UPDRS"])

In [302]:
df

test_time  motor_UPDRS  Jitter_8_  Jitter_Abs_  Jitter_RAP  Jitter_PPQ5  \
0        5.6431       28.199    0.00662     0.000034     0.00401      0.00317   
1       12.6660       28.447    0.00300     0.000017     0.00132      0.00150   
2       19.6810       28.695    0.00481     0.000025     0.00205      0.00208   
3       25.6470       28.905    0.00528     0.000027     0.00191      0.00264   
4       33.6420       29.187    0.00335     0.000020     0.00093      0.00130   
...         ...          ...        ...          ...         ...          ...   
5870   142.7900       22.485    0.00406     0.000031     0.00167      0.00168   
5871   149.8400       21.988    0.00297     0.000025     0.00119      0.00147   
5872   156.8200       21.495    0.00349     0.000025     0.00152      0.00187   
5873   163.7300       21.007    0.00281     0.000020     0.00128      0.00151   
5874   170.7300       20.513    0.00282     0.000021     0.00135      0.00166   

      Jitter_DDP  Shimmer  Shimmer_dB_  Shimmer_APQ3  Shimmer_APQ5  \
0        0.01204  0.02565        0.230       0.01438       0.01309   
1        0.00395  0.02024        0.179       0.00994       0.01072   
2        0.00616  0.01675        0.181       0.00734       0.00844   
3        0.00573  0.02309        0.327       0.01106       0.01265   
4        0.00278  0.01703        0.176       0.00679       0.00929   
...          ...      ...          ...           ...           ...   
5870     0.00500  0.01896        0.160       0.00973       0.01133   
5871     0.00358  0.02315        0.215       0.01052       0.01277   
5872     0.00456  0.02499        0.244       0.01371       0.01456   
5873     0.00383  0.01484        0.131       0.00693       0.00870   
5874     0.00406  0.01907        0.171       0.00946       0.01154   

      Shimmer_APQ11  Shimmer_DDA       NHR     HNR     RPDE      DFA      PPE  
0           0.01662      0.04314  0.014290  21.640  0.41888  0.54842  0.16006  
1           0.01689      0.02982  0.011112  27.183  0.43493  0.56477  0.10810  
2           0.01458      0.02202  0.020220  23.047  0.46222  0.54405  0.21014  
3           0.01963      0.03317  0.027837  24.445  0.48730  0.57794  0.33277  
4           0.01819      0.02036  0.011625  26.126  0.47188  0.56122  0.19361  
...             ...          ...       ...     ...      ...      ...      ...  
5870        0.01549      0.02920  0.025137  22.369  0.64215  0.55314  0.21367  
5871        0.01904      0.03157  0.011927  22.886  0.52598  0.56518  0.12621  
5872        0.01877      0.04112  0.017701  25.065  0.47792  0.57888  0.14157  
5873        0.01307      0.02078  0.007984  24.422  0.56865  0.56327  0.14204  
5874        0.01470      0.02839  0.008172  23.259  0.58608  0.57077  0.15336  

[5875 rows x 18 columns]

In [303]:
scaled_df, train_df, test_df = scale_split_df(
    df, 'motor_UPDRS', 0.2, DATA_DIR, scaled_file_name, train_file_name, test_file_name, scaler_params_file)
scaled_df.describe()

test_time     Jitter_8_   Jitter_Abs_    Jitter_RAP   Jitter_PPQ5  \
count  5.875000e+03  5.875000e+03  5.875000e+03  5.875000e+03  5.875000e+03   
mean   3.507360e-17  1.451321e-16  1.161057e-16  1.935095e-17 -1.935095e-17   
std    1.000085e+00  1.000085e+00  1.000085e+00  1.000085e+00  1.000085e+00   
min   -1.817446e+00 -9.466570e-01 -1.161111e+00 -8.506930e-01 -7.629815e-01   
25%   -8.610650e-01 -4.576594e-01 -6.001095e-01 -4.505077e-01 -3.904491e-01   
50%   -2.508787e-02 -2.229405e-01 -2.639533e-01 -2.360084e-01 -2.108831e-01   
75%    8.529263e-01  1.149124e-01  2.586939e-01  9.694579e-02  4.908555e-02   
max    2.294608e+00  1.668571e+01  1.116063e+01  1.746499e+01  1.776448e+01   

         Jitter_DDP       Shimmer   Shimmer_dB_  Shimmer_APQ3  Shimmer_APQ5  \
count  5.875000e+03  5.875000e+03  5.875000e+03  5.875000e+03  5.875000e+03   
mean   1.693208e-16  1.741586e-16  1.838340e-16  4.837738e-17  1.548076e-16   
std    1.000085e+00  1.000085e+00  1.000085e+00  1.000085e+00  1.000085e+00   
min   -8.517702e-01 -1.199058e+00 -1.237697e+00 -1.174502e+00 -1.092523e+00   
25%   -4.515863e-01 -5.773716e-01 -5.905295e-01 -5.950218e-01 -5.613909e-01   
50%   -2.360206e-01 -2.525927e-01 -2.517438e-01 -2.610839e-01 -2.523139e-01   
75%    9.693236e-02  2.212206e-01  2.347177e-01  2.583332e-01  2.167030e-01   
max    1.746598e+01  9.081220e+00  7.800931e+00  1.099383e+01  8.814745e+00   

       Shimmer_APQ11   Shimmer_DDA           NHR           HNR          RPDE  \
count   5.875000e+03  5.875000e+03  5.875000e+03  5.875000e+03  5.875000e+03   
mean   -3.870190e-17  9.675476e-17 -3.870190e-17 -6.385814e-16  1.935095e-16   
std     1.000085e+00  1.000085e+00  1.000085e+00  1.000085e+00  1.000085e+00   
min    -1.250516e+00 -1.174245e+00 -5.333439e-01 -4.665987e+00 -3.866744e+00   
25%    -5.912529e-01 -5.952688e-01 -3.545954e-01 -5.298620e-01 -7.099418e-01   
50%    -2.387287e-01 -2.608275e-01 -2.290577e-01  5.605219e-02  7.695473e-03   
75%     2.619106e-01  2.585891e-01 -1.100432e-02  6.442969e-01  7.186976e-01   
max     1.240861e+01  1.099408e+01  1.199822e+01  3.774533e+00  4.204980e+00   

                DFA           PPE  motor_UPDRS  
count  5.875000e+03  5.875000e+03  5875.000000  
mean   4.450719e-16  1.741586e-16    21.296229  
std    1.000085e+00  1.000085e+00     8.129282  
min   -1.963436e+00 -2.159850e+00     5.037700  
25%   -8.048365e-01 -6.913181e-01    15.000000  
50%   -1.359690e-01 -1.539957e-01    20.871000  
75%    8.194450e-01  4.907692e-01    27.596500  
max    2.995380e+00  5.597736e+00    39.511000

In [304]:
train_df = pd.read_csv("data/telemetry/train_telemetry_scaled.csv")
test_df = pd.read_csv("data/telemetry/test_telemetry_scaled.csv")

In [305]:

X_train = train_df.loc[:, train_df.columns != 'motor_UPDRS']
y_train = train_df.loc[:, train_df.columns == 'motor_UPDRS']
X_test = test_df.loc[:, test_df.columns != 'motor_UPDRS']
y_test = test_df.loc[:, test_df.columns == 'motor_UPDRS']

In [306]:
X_test

test_time  Jitter_8_  Jitter_Abs_  Jitter_RAP  Jitter_PPQ5  Jitter_DDP  \
0     -1.535313  -0.345634    -0.316204   -0.184785    -0.224284   -0.183730   
1      1.421497   4.994219     5.700422    5.549070     3.088307    5.547970   
2      1.548553  -0.167817    -0.373458   -0.107949    -0.213563   -0.106895   
3      1.545559  -0.178486    -0.445164   -0.194389    -0.243044   -0.194401   
4     -1.544893  -0.281620    -0.086356   -0.556157    -0.326127   -0.555101   
...         ...        ...          ...         ...          ...         ...   
1170  -1.130474  -0.404314    -0.620537   -0.293635    -0.331487   -0.294714   
1171  -0.452381  -0.212271    -0.472679   -0.130359    -0.200163   -0.131439   
1172   0.756091  -0.361638    -0.702805   -0.184785    -0.315407   -0.184797   
1173   0.111979  -0.580353    -0.853998   -0.511336    -0.457451   -0.512414   
1174  -1.430038  -0.276286    -0.677791   -0.364068    -0.302006   -0.363012   

       Shimmer  Shimmer_dB_  Shimmer_APQ3  Shimmer_APQ5  Shimmer_APQ11  \
0     0.276189     0.199970      0.419636      0.441459       0.218627   
1     2.565513     2.888539      2.698271      1.663964       2.091083   
2    -0.179043    -0.064977     -0.094115     -0.273319      -0.457399   
3    -0.556468    -0.560126     -0.542136     -0.477370      -0.594505   
4    -0.590146    -0.620933     -0.764257     -0.598000      -0.374835   
...        ...          ...           ...           ...            ...   
1170 -0.551823    -0.564469     -0.549691     -0.533184      -0.686077   
1171  0.079928    -0.004170      0.237557     -0.026658      -0.089613   
1172 -0.622275    -0.534065     -0.588978     -0.604602      -0.742120   
1173 -0.695438    -0.681741     -0.644130     -0.716229      -0.872221   
1174  0.228188     0.308556      0.253422      0.239209       0.208619   

      Shimmer_DDA       NHR       HNR      RPDE       DFA       PPE  
0        0.419640 -0.346470 -0.379072 -1.197923  1.679649 -0.418831  
1        2.698021  1.756660 -2.025178  1.254413  1.487819  3.585400  
2       -0.094111 -0.284162  0.093575 -0.020925  0.194374  0.403329  
3       -0.542383 -0.240651  1.240466  0.089793  1.144499  0.315342  
4       -0.764252 -0.298553  0.301465  0.573764 -0.218343 -0.284391  
...           ...       ...       ...       ...       ...       ...  
1170    -0.549938 -0.315559  1.425283 -1.900656 -0.878042 -1.004465  
1171     0.237309 -0.236212  0.215932 -0.407547 -0.938130 -0.201323  
1172    -0.588721 -0.336602  1.205973 -0.832197 -0.674223 -0.670442  
1173    -0.644125 -0.075088  1.188260 -0.866561 -1.452405 -1.489793  
1174     0.253678 -0.175998 -0.679720  0.005220 -1.091877 -0.024693  

[1175 rows x 17 columns]

In [307]:
grid_params = {
    'max_depth': [1, 2, 3, 4],
    'eta': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9],
    'subsample': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
}

In [308]:
grid_params_big = {
    'max_depth': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10],
    'eta': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9],
    'subsample': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
}

In [ ]:
%%time
best = grid_search(grid_params, X_train, y_train, X_test, y_test, num_boost_round=40)

In [267]:
best.best_params_

{'eta': 0.3, 'max_depth': 4, 'subsample': 0.8}

In [268]:
len(best.best_estimator_.get_booster().get_dump())

40

In [ ]:
%%time
best = grid_search(grid_params_big, X_train, y_train, X_test, y_test, num_boost_round=20)

In [270]:
best.best_params_

{'eta': 0.2, 'max_depth': 9, 'subsample': 0.8}

In [271]:
len(best.best_estimator_.get_booster().get_dump())

20

In [272]:
dtrain = xgb.DMatrix(X_train, label=y_train)
dtest = xgb.DMatrix(X_test, label=y_test)

/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:384: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype):
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:359: FutureWarning: is_categorical_dtype is deprecated and will be removed in a

In [273]:
grid_params_single = {
    'max_depth': [3],
    'eta': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9],
    'subsample': [0.01, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
}

In [274]:
%%time
best = grid_search(grid_params_single, X_train, y_train, X_test, y_test, num_boost_round=1)

/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:384: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype):
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:359: FutureWarning: is_categorical_dtype is deprecated and will be removed in a

CPU times: user 1.07 s, sys: 140 ms, total: 1.21 s
Wall time: 4.6 s


/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:384: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype):
/home/mateusz/Documents/tmp/prediction-gap/venv/lib/python3.10/site-packages/xgboost/data.py:359: FutureWarning: is_categorical_dtype is deprecated and will be removed in a

In [275]:
best.best_params_

{'eta': 0.9, 'max_depth': 3, 'subsample': 0.8}

In [276]:
len(best.best_estimator_.get_booster().get_dump())

1

In [277]:
param_big= {
    'eta': 0.2,
    'max_depth': 7,
    'objective': 'reg:squarederror',
    'seed': 42,
    'subsample': 0.8,
}
steps = 20

In [278]:
%%time
train_and_save_model(param_big, steps, dtrain, dtest, MODEL_PATH, telemetry_model_name + '_big')

[0]	test-rmse:7.74401	train-rmse:7.54965
[19]	test-rmse:6.41928	train-rmse:4.64089
CPU times: user 2.32 s, sys: 0 ns, total: 2.32 s
Wall time: 165 ms


In [293]:
param = {
    'eta': 0.2,
    'max_depth': 4,
    'objective': 'reg:squarederror',
    'seed': 42,
    'subsample': 0.8,
}
steps = 40

In [294]:
%%time
train_and_save_model(param, steps, dtrain, dtest, MODEL_PATH, telemetry_model_name )

[0]	test-rmse:7.89711	train-rmse:7.85245
[39]	test-rmse:6.76884	train-rmse:5.86271
CPU times: user 11.3 s, sys: 16.9 ms, total: 11.3 s
Wall time: 854 ms


In [295]:
param_single = {
    'eta': 0.9,
    'max_depth': 3,
    'objective': 'reg:squarederror',
    'seed': 42,
    'subsample': 0.9,
}
steps=1

In [296]:
%%time
train_and_save_model(param_single, steps, dtrain, dtest, MODEL_PATH, telemetry_model_name+'_single' )

[0]	test-rmse:7.65970	train-rmse:7.56464
CPU times: user 3.58 s, sys: 6.62 ms, total: 3.58 s
Wall time: 282 ms
